In [2]:
import pandas as pd
import matplotlib.pyplot as plt

conf_key = {'CHI':1163450153, 'CSCW':1195049314, 'UBI':1171345118, 'UIST':1166315290}

ori_paperyear_conf = {}
ori_citingpatent_conf = {}

In [3]:
# join paperid with paperyear and papercitation2science
df_year = pd.read_csv('../data/paperyear_result.tsv', usecols=[1,2])
df_paperid = pd.read_csv('../data/HCI_paperids.tsv', sep='\t')
df_paper_year = df_year.merge(df_paperid)

df_papercitation2science = pd.read_csv('../data/papercitationscience_result.tsv', usecols=[3,4])
df_paper_pc2s = df_papercitation2science.merge(df_paperid)

for conf_name,conf_id in conf_key.items():
    ori_paperyear_conf[conf_name] = df_paper_year.loc[df_paper_year['confid']==conf_id]
    ori_citingpatent_conf[conf_name] = df_paper_pc2s.loc[df_paper_pc2s['confid']==conf_id]

ori_citingpatent_conf['CHI'].head(5)

paperid    patent      confid
0  2134161165  10001804  1163450153
1  2134161165   6024576  1163450153
2  2134161165   6028593  1163450153
3  2134161165   6057828  1163450153
4  2134161165   6078308  1163450153

In [4]:
paperyear_map_conf = {}
inv_paperyear_map_conf = {}
for conf, df in ori_paperyear_conf.items():
    paperyear_map = {}
    inv_paperyear_map = {}
    for row in df.iterrows():
        paperid = str(row[1]).split(',')[0].split('\n')[0].split()[1] # paperid
        paperyear = str(row[1]).split(',')[0].split('\n')[1].split()[1] # paperyear 
        if paperyear not in paperyear_map.keys():
            paperyear_map[paperyear] = []    
        if paperid not in paperyear_map[paperyear]:
            paperyear_map[paperyear].append(paperid)
        inv_paperyear_map[paperid] = paperyear
    paperyear_map_conf[conf] = paperyear_map
    inv_paperyear_map_conf[conf] = inv_paperyear_map
print(">>> done paper year map construction")

>>> done paper year map construction


In [5]:
citingpatent_map_conf = {}
citedpaper_map_conf = {}
for conf, df in ori_citingpatent_conf.items():
    citingpatent_map = {}
    citedpaper_map = {}
    inv_paperyear_map = inv_paperyear_map_conf[conf]
    for row in df.iterrows():
        paperid = str(row[1]).split(',')[0].split('\n')[0].split()[1] # paperid
        patentid = str(row[1]).split(',')[0].split('\n')[1].split()[1] # patentid
        # paperyear
        paperyear = inv_paperyear_map[paperid]
        if paperyear not in citingpatent_map.keys():
            citingpatent_map[paperyear] = []
        if paperyear not in citedpaper_map.keys():
            citedpaper_map[paperyear] = []  
        citingpatent_map[paperyear].append(patentid)
        # unique cited paper this year
        if paperid not in citedpaper_map[paperyear]:
            citedpaper_map[paperyear].append(paperid)
    citingpatent_map_conf[conf] = citingpatent_map
    citedpaper_map_conf[conf] = citedpaper_map
print(">>> done citing data")

>>> done citing data


In [6]:
# Visualization
fig = plt.figure(figsize=(100,100))
axes = fig.subplots(nrows=4, ncols=2)
for ax in axes:
    ax[0].set_ylabel("count", fontsize=50)
    ax[1].set_ylabel("portion", fontsize=50)
    for ax_c in ax:
        ax_c.set_xlabel("paper_year", fontsize=50)
        ax_c.tick_params(labelsize=50)

plot_idx = 0

X_year = [i for i in range (1950, 2021)]

for conf, paperyear_map in paperyear_map_conf.items():
    Y_papercnt = [0] * 71
    Y_citingpatentcnt = [0] * 71
    Y_citedportion = [0.0] * 71

    citingpatent_map = citingpatent_map_conf[conf]
    citedpaper_map = citedpaper_map_conf[conf]
    for i in range (1950, 2021):
        if str(i) in paperyear_map.keys():
            Y_papercnt[i-1950] = len(paperyear_map[str(i)])
        if str(i) in citingpatent_map.keys():
            Y_citingpatentcnt[i-1950] = len(citingpatent_map[str(i)])    
        if str(i) in citedpaper_map.keys():
            Y_citedportion[i-1950] = len(citedpaper_map[str(i)]) / Y_papercnt[i-1950]
    axes[plot_idx, 0].plot(X_year,Y_papercnt,color='r')
    axes[plot_idx, 0].plot(X_year,Y_citingpatentcnt,color='g')
    axes[plot_idx, 0].set_title('conference_{}'.format(conf), fontsize=90)
    axes[plot_idx, 1].plot(X_year,Y_citedportion,color='b')
    axes[plot_idx, 1].set_title('conference_{}'.format(conf), fontsize=90)
    plot_idx += 1